In [5]:
%pip install torch torchvision torchaudio
%pip install matplotlib pandas scikit-learn tqdm


import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from torchvision import models, transforms
from PIL import Image
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import ast
import random
from tqdm import tqdm
from collections import Counter


transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])


class FashionDataset(Dataset):
    def __init__(self, dataframe, image_dir, transform=None):
        self.dataframe = dataframe
        self.image_dir = image_dir
        self.transform = transform
        self.label_columns = [col for col in dataframe.columns if col != 'image_filename']

    def __len__(self):
        return len(self.dataframe)

    def __getitem__(self, idx):
        row = self.dataframe.iloc[idx]
        img_path = os.path.join(self.image_dir, row['image_filename'])
        image = Image.open(img_path).convert("RGB")
        if self.transform:
            image = self.transform(image)
        labels = torch.tensor(row[self.label_columns].fillna(0).astype(float).values, dtype=torch.float32)
        labels = torch.clamp(labels, 0.0, 1.0)
        return image, labels


labels_df = pd.read_csv("/Users/user/Downloads/ClothingAttributeDataset/labels.csv")
image_dir = "/Users/user/Downloads/ClothingAttributeDataset/images"
dataset = FashionDataset(labels_df, image_dir=image_dir, transform=transform)
dataloader = DataLoader(dataset, batch_size=32, shuffle=True)
label_names = [col for col in labels_df.columns if col != 'image_filename']

# Define Model
num_labels = len(label_names)
model = models.resnet18(pretrained=True)
model.fc = nn.Sequential(
    nn.Linear(model.fc.in_features, 512),
    nn.ReLU(),
    nn.Dropout(0.3),
    nn.Linear(512, num_labels),
    nn.Sigmoid()
)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = model.to(device)


criterion = nn.BCELoss()
optimizer = optim.Adam(model.parameters(), lr=1e-4)


epochs = 5
for epoch in range(epochs):
    model.train()
    running_loss = 0.0
    for images, labels in dataloader:
        images = images.to(device)
        labels = labels.to(device)
        outputs = model(images)
        loss = criterion(outputs, labels)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        running_loss += loss.item()
    avg_loss = running_loss / len(dataloader)
    print(f"Epoch {epoch+1}/{epochs}, Loss: {avg_loss:.4f}")


torch.save(model.state_dict(), "fashion_trend_model.pt")


model.load_state_dict(torch.load("fashion_trend_model.pt"))
model.eval()


batch_predictions = []
for idx, row in tqdm(labels_df.iterrows(), total=len(labels_df)):
    filename = row['image_filename']
    img_path = os.path.join(image_dir, filename)
    try:
        image = Image.open(img_path).convert("RGB")
    except:
        continue
    input_tensor = transform(image).unsqueeze(0).to(device)
    with torch.no_grad():
        output = model(input_tensor)
        preds = (output > 0.9).int().cpu().squeeze().numpy()
    predicted_labels = [label_names[i] for i, val in enumerate(preds) if val == 1]
    batch_predictions.append({
        'image_filename': filename,
        'predicted_labels': predicted_labels
    })
predictions_df = pd.DataFrame(batch_predictions)
predictions_df.to_csv("fashion_predictions.csv", index=False)

# Map to Readable Labels
label_map = {
    "category_1.0": "Shirt", "category_2.0": "Sweater", "category_3.0": "T-shirt",
    "category_4.0": "Outerwear", "category_5.0": "Suit", "category_6.0": "Tank Top",
    "category_7.0": "Dress", "sleeve_1.0": "No sleeves", "sleeve_2.0": "Short sleeves",
    "sleeve_3.0": "Long sleeves", "neckline_1.0": "Crew neck", "neckline_2.0": "V-neck",
    "neckline_3.0": "Turtleneck", "pattern_graphics": "Graphic pattern", "pattern_plaid": "Plaid",
    "pattern_stripe": "Stripes", "pattern_spot": "Spots", "pattern_floral": "Floral",
    "pattern_solid": "No pattern", "placket": "Placket", "necktie": "Necktie",
    "scarf": "Scarf", "skin_exposure": "Exposed skin", "gender": "Gender (misc.)",
    "many_colors": "Many colors", "black": "Black", "white": "White", "red": "Red",
    "blue": "Blue", "green": "Green", "yellow": "Yellow", "purple": "Purple",
    "brown": "Brown", "cyan": "Cyan", "gray": "Gray"
}

predictions_df['readable_labels'] = predictions_df['predicted_labels'].apply(
    lambda labels: [label_map.get(label, label) for label in labels]
)


df = predictions_df.explode('readable_labels')
df = df.rename(columns={'readable_labels': 'label'})
trend_map = {
    "Graphic pattern": "Pattern Clash Renaissance", "Plaid": "Pattern Clash Renaissance",
    "Floral": "Pattern Clash Renaissance", "Stripes": "Pattern Clash Renaissance",
    "Spots": "Pattern Clash Renaissance", "Many colors": "Pattern Clash Renaissance",
    "Placket": "Soft Power Dressing", "Necktie": "Soft Power Dressing",
    "Scarf": "Soft Power Dressing", "Turtleneck": "Soft Power Dressing",
    "Shirt": "Soft Power Dressing", "Suit": "Soft Power Dressing",
    "Exposed skin": "Sensual Softness", "No sleeves": "Sensual Softness",
    "Tank Top": "Sensual Softness", "V-neck": "Sensual Softness"
}
df['trend_group'] = df['label'].apply(lambda x: trend_map.get(x, 'Other'))
df.to_csv("fashion_predictions_cleaned.csv", index=False)


Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


/Users/user/fashion-env/lib/python3.10/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/user/fashion-env/lib/python3.10/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet18_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  la

Epoch 1/5, Loss: 0.3844


/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = torch.tensor(row[self.label_columns].fillna(0).astype(float).values, dtype=torch.float32)
/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = torch.tensor(row[self.label_columns].fillna(0).astype(float).values, dtype=torch.float32)
/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downca

Epoch 2/5, Loss: 0.2469


...

/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = torch.tensor(row[self.label_columns].fillna(0).astype(float).values, dtype=torch.float32)
/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = torch.tensor(row[self.label_columns].fillna(0).astype(float).values, dtype=torch.float32)
/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downca

Epoch 4/5, Loss: 0.1662


/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = torch.tensor(row[self.label_columns].fillna(0).astype(float).values, dtype=torch.float32)
/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = torch.tensor(row[self.label_columns].fillna(0).astype(float).values, dtype=torch.float32)
/var/folders/8y/z61_gqh53bl7b6583985l8h00000gn/T/ipykernel_24830/3509390684.py:45: FutureWarning: Downca

Epoch 5/5, Loss: 0.1388


100%|███████████████████████████████████████| 1856/1856 [01:19<00:00, 23.46it/s]


In [2]:
label_counts = labels_df[label_names].sum().sort_values(ascending=False)
print(label_counts)


category            4866.0
sleevelength        4644.0
placket             2942.0
gender              2826.0
pattern_solid       2545.0
black               2364.0
collar              2357.0
neckline            2225.0
white               2210.0
gray                2089.0
necktie             1950.0
many_colors         1947.0
brown               1912.0
scarf               1900.0
blue                1894.0
pattern_graphics    1888.0
skin_exposure       1883.0
pattern_plaid       1845.0
red                 1837.0
cyan                1834.0
green               1827.0
purple              1821.0
pattern_spot        1821.0
pattern_stripe      1814.0
yellow              1811.0
pattern_floral      1787.0
dtype: float64
